# Install

In [22]:
# https://stackoverflow.com/questions/56081324/why-are-google-colab-shell-commands-not-working
import locale
def getpreferredencoding(do_setlocale = True):
    return "UTF-8"
locale.getpreferredencoding = getpreferredencoding

In [23]:
!pip install -q -U bitsandbytes
!pip install -q -U git+https://github.com/huggingface/transformers.git
!pip install -q -U git+https://github.com/huggingface/peft.git
!pip install -q -U git+https://github.com/huggingface/accelerate.git
!pip install -q -U einops
!pip install -q -U safetensors
!pip install -q -U torch
!pip install -q -U xformers
!pip install -q -U datasets

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


In [25]:
!pip install auto_gptq

In [26]:
!pip install sentencepiece

# Import

In [27]:
from transformers import AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig, pipeline
import transformers
import torch
from torch.utils.data import DataLoader, Dataset
import torch
from transformers import AutoTokenizer
from auto_gptq import AutoGPTQForCausalLM

# Load Quantized Model

In [30]:
model_id = "rnosov/WizardLM-Uncensored-Falcon-7b-sharded" # sharded model by vilsonrodrigues
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_use_double_quant=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16
)

tokenizer = AutoTokenizer.from_pretrained(model_id,use_fast=False)
tokenizer.pad_token = tokenizer.eos_token
model = AutoModelForCausalLM.from_pretrained(model_id, quantization_config=bnb_config, device_map={"":0}, trust_remote_code=True)

A new version of the following files was downloaded from https://huggingface.co/ehartford/WizardLM-Uncensored-Falcon-7b:
- configuration_RW.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


A new version of the following files was downloaded from https://huggingface.co/ehartford/WizardLM-Uncensored-Falcon-7b:
- modelling_RW.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


Loading checkpoint shards:   0%|          | 0/15 [00:00<?, ?it/s]

In [31]:
from peft import prepare_model_for_kbit_training

model.gradient_checkpointing_enable()
model = prepare_model_for_kbit_training(model)

In [32]:
def print_trainable_parameters(model):
    """
    Prints the number of trainable parameters in the model.
    """
    trainable_params = 0
    all_param = 0
    for _, param in model.named_parameters():
        all_param += param.numel()
        if param.requires_grad:
            trainable_params += param.numel()
    print(
        f"trainable params: {trainable_params} || all params: {all_param} || trainable%: {100 * trainable_params / all_param}"
    )

In [33]:
from peft import LoraConfig, get_peft_model

config = LoraConfig(
    r=16,
    lora_alpha=32,
    target_modules=["query_key_value"],
    lora_dropout=0.05,
    bias="none",
    task_type="CAUSAL_LM"
)

model = get_peft_model(model, config)
print_trainable_parameters(model)

trainable params: 4718592 || all params: 3613467968 || trainable%: 0.13058347387569813


# Prepare Data

In [34]:
from datasets import load_dataset

data = load_dataset("zadhart/ESG_Chat")

Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Dataset csv downloaded and prepared to /root/.cache/huggingface/datasets/zadhart___csv/zadhart--ESG_Chat-ca993bc16abb0d1a/0.0.0/eea64c71ca8b46dd3f537ed218fc9bf495d5707789152eb2764f5c78fa66d59d. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

In [35]:
tokenizer.pad_token = tokenizer.eos_token

# prompt_template = "### Instruction: {prompt}\n### Response:"

train_dataset = data['train'].map(lambda x: {"input_text": x['Perguntas']  + "\n" + x['Respostas']})

# Tokenize the datasets
train_encodings = tokenizer(train_dataset['input_text'], truncation=True, padding=True, max_length=256, return_tensors='pt')

Map:   0%|          | 0/183 [00:00<?, ? examples/s]

In [36]:
class TextDataset(Dataset):
    def __init__(self, encodings):
        self.encodings = encodings

    def __getitem__(self, idx):
        item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()}
        item["labels"] = item["input_ids"].clone()
        return item

    def __len__(self):
        return len(self.encodings["input_ids"])


In [37]:
# Convert the encodings to PyTorch datasets
train_dataset = TextDataset(train_encodings)

# Example Before Fine Tuning

In [46]:
def generate(index):

  example_text = data['train'][index]['Perguntas']
  correct_answer = data['train'][index]['Respostas']

  print("Question:")
  print(example_text)

  encoding = tokenizer(example_text, return_tensors="pt").to("cuda:0")
  output = model.generate(input_ids=encoding.input_ids, attention_mask=encoding.attention_mask, max_new_tokens=150, do_sample=True, temperature=0.000001, eos_token_id=tokenizer.eos_token_id, top_k = 0)
  predict = tokenizer.decode(output[0], skip_special_tokens=True)
  predict = predict[len(example_text)+1:]
  print("Answer:")
  print(predict)

  print("Best Answer:")
  print(correct_answer)

  print()

In [50]:
import random
random.seed(10)
rand_q = random.sample(list(range(len(data['train']))),10)

In [53]:
def get_response_set(model):
   predictions = []

   for index in rand_q:
      example_text = data['train'][index]['Perguntas']
      encoding = tokenizer(example_text, return_tensors="pt").to("cuda:0")
      output = model.generate(input_ids=encoding.input_ids, attention_mask=encoding.attention_mask, max_new_tokens=150, do_sample=True, temperature=0.000001, eos_token_id=tokenizer.eos_token_id, top_k = 0)
      predict = tokenizer.decode(output[0], skip_special_tokens=True)
      predict = predict[len(example_text)+1:]
      predictions.append(predict)

   return predictions


In [47]:
generate(39)

Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.


Question:
Define emissions in ESG context
Answer:
Emissions are the release of pollutants, greenhouse gases, or other environmental contaminants into the atmosphere, water, or soil. In the context of ESG, emissions refer to the environmental impact of a company's operations, products, or services. This includes the direct emissions from a company's facilities, transportation, and energy use, as well as the indirect emissions from the production of raw materials, supply chain emissions, and the use of products by customers. The goal of ESG is to reduce the negative environmental impact of companies and their products, and to promote sustainable practices.
Best Answer:
Emissions in the ESG (Environmental Social and Governance) context refer to the release of harmful gases or pollutants into the environment which contribute to climate change and related environmental impacts. Emissions can come from a variety of sources including industrial facilities transportation energy production and 

In [54]:
predictions = get_response_set(model)

Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.


In [56]:
predictions

['Sustainability is a term that refers to the ability of a business or organization to operate in a way that meets the needs of the present without compromising the ability of future generations to meet their own needs. In the context of ESG (Environmental, Social, and Governance) investing, sustainability is often defined as the ability of a company to balance economic growth with environmental protection and social responsibility. This includes factors such as reducing carbon emissions, minimizing waste, promoting fair labor practices, and supporting local communities. In other words, sustainability is about creating long-term value for all stakeholders, including shareholders, employees, customers, and the broader community.',
 "Chief Financial Officers (CFOs) play a critical role in the ESG context, as they are responsible for managing the financial resources of a company and ensuring that it operates in an environmentally, socially, and financially sustainable manner. In addition 

In [59]:
reference = data["train"]["Respostas"]

In [63]:
references = []
questions = []
for i in rand_q:
   references.append(reference[i])
   questions.append(data['train'][i]['Perguntas'])

references

["Sustainability in the ESG (Environmental Social and Governance) context refers to a company's ability to operate in a manner that meets the needs of the present generation without compromising the ability of future generations to meet their needs. This concept takes into account various environmental social and governance factors that impact companies' long-term viability and ability to create value.\n\nFrom an environmental perspective sustainable practices aim to reduce a company's negative impact on the environment such as carbon emissions waste generation and resource consumption. From a social standpoint sustainability involves ethical and responsible conduct respecting human rights creating a safe and healthy workplace providing fair wages and supporting diversity and inclusion. Finally from a governance perspective sustainability involves establishing clear policies and processes to ensure accountability transparency and ethical conduct at all levels of the organization.\n\nOv

In [65]:
import pandas as pd

def compare_df(question,pred,ref) -> pd.DataFrame:
   info = {
      "quetsion" : question,
      "response" : pred,
      "answer" : ref,
   }

   return pd.DataFrame(info)


df = compare_df(questions,predictions,references)

In [71]:
!pip install evaluate
!pip install rouge_score

  Preparing metadata (setup.py) ... done
  Created wheel for rouge_score: filename=rouge_score-0.1.2-py3-none-any.whl size=24934 sha256=2eb6e4dd816607331295ef7b620ac2bea175cd94cea3936da9c0c940c8b3c091
  Stored in directory: /root/.cache/pip/wheels/5f/dd/89/461065a73be61a532ff8599a28e9beef17985c9e9c31e541b4
Successfully built rouge_score


In [67]:
df.head()

quetsion  \
0            Define sustainability in ESG context   
1  Define Chief Financial Officers in ESG context   
2                Define Green Deal in ESG context   
3    Define indigenous communities in ESG context   
4            Define B Impact Score in ESG context   

                                            response  \
0  Sustainability is a term that refers to the ab...   
1  Chief Financial Officers (CFOs) play a critica...   
2  Green Deal is a European Union initiative aime...   
3  Indigenous communities are groups of people wh...   
4  B Impact Score is a tool that measures the imp...   

                                              answer  
0  Sustainability in the ESG (Environmental Socia...  
1  Chief Financial Officers (CFOs) in the ESG con...  
2  The Green Deal refers to a set of policies and...  
3  Indigenous communities refer to groups of peop...  
4  The B Impact Score is a comprehensive rating s...

import numpy as np
from google.colab import autoviz
df_2885174110291172259 = autoviz.get_registered_df('df_2885174110291172259')

def categorical_histogram(df, colname, figsize=(2, 1.2), mpl_palette_name='Dark2'):
  from matplotlib import pyplot as plt
  import seaborn as sns
  _, ax = plt.subplots(figsize=figsize)
  bars = df[colname].value_counts()
  plt.barh(bars.index, bars.values, color=sns.palettes.mpl_palette(mpl_palette_name))
  plt.title(colname)
  ax.spines[['top', 'right',]].set_visible(False)
  return autoviz.MplChart.from_current_mpl_state()

chart = categorical_histogram(df_2885174110291172259, *['quetsion'], **{})
chart

import numpy as np
from google.colab import autoviz
df_2885174110291172259 = autoviz.get_registered_df('df_2885174110291172259')

def categorical_histogram(df, colname, figsize=(2, 1.2), mpl_palette_name='Dark2'):
  from matplotlib import pyplot as plt
  import seaborn as sns
  _, ax = plt.subplots(figsize=figsize)
  bars = df[colname].value_counts()
  plt.barh(bars.index, bars.values, color=sns.palettes.mpl_palette(mpl_palette_name))
  plt.title(colname)
  ax.spines[['top', 'right',]].set_visible(False)
  return autoviz.MplChart.from_current_mpl_state()

chart = categorical_histogram(df_2885174110291172259, *['response'], **{})
chart

import numpy as np
from google.colab import autoviz
df_2885174110291172259 = autoviz.get_registered_df('df_2885174110291172259')

def categorical_histogram(df, colname, figsize=(2, 1.2), mpl_palette_name='Dark2'):
  from matplotlib import pyplot as plt
  import seaborn as sns
  _, ax = plt.subplots(figsize=figsize)
  bars = df[colname].value_counts()
  plt.barh(bars.index, bars.values, color=sns.palettes.mpl_palette(mpl_palette_name))
  plt.title(colname)
  ax.spines[['top', 'right',]].set_visible(False)
  return autoviz.MplChart.from_current_mpl_state()

chart = categorical_histogram(df_2885174110291172259, *['answer'], **{})
chart

import numpy as np
from google.colab import autoviz
df_2885174110291172259 = autoviz.get_registered_df('df_2885174110291172259')

def heatmap(df, x_colname, y_colname, figsize=(2, 2), mpl_palette_name='viridis'):
  from matplotlib import pyplot as plt
  import seaborn as sns
  import pandas as pd
  plt.subplots(figsize=figsize)
  df_2dhist = pd.DataFrame({
      x_label: grp[y_colname].value_counts()
      for x_label, grp in df.groupby(x_colname)
  })
  sns.heatmap(df_2dhist, cmap=mpl_palette_name)
  plt.xlabel(x_colname)
  plt.ylabel(y_colname)
  return autoviz.MplChart.from_current_mpl_state()

chart = heatmap(df_2885174110291172259, *['quetsion', 'response'], **{})
chart

...

import numpy as np
from google.colab import autoviz
df_520743312088167719 = autoviz.get_registered_df('df_520743312088167719')

def violin_plot(df, value_colname, facet_colname, col_width=.3, col_length=3, mpl_palette_name='Dark2', **kwargs):
  from matplotlib import pyplot as plt
  import seaborn as sns
  plt.figure(figsize=(col_length, col_width * len(df[facet_colname].unique())))
  sns.violinplot(df, x=value_colname, y=facet_colname, palette=mpl_palette_name, **kwargs)
  sns.despine(top=True, right=True, bottom=True, left=True)
  return autoviz.MplChart.from_current_mpl_state()

chart = violin_plot(df_520743312088167719, *['index', 'response'], **{'inner': 'stick'})
chart

import numpy as np
from google.colab import autoviz
df_520743312088167719 = autoviz.get_registered_df('df_520743312088167719')

def violin_plot(df, value_colname, facet_colname, col_width=.3, col_length=3, mpl_palette_name='Dark2', **kwargs):
  from matplotlib import pyplot as plt
  import seaborn as sns
  plt.figure(figsize=(col_length, col_width * len(df[facet_colname].unique())))
  sns.violinplot(df, x=value_colname, y=facet_colname, palette=mpl_palette_name, **kwargs)
  sns.despine(top=True, right=True, bottom=True, left=True)
  return autoviz.MplChart.from_current_mpl_state()

chart = violin_plot(df_520743312088167719, *['index', 'answer'], **{'inner': 'stick'})
chart

import numpy as np
from google.colab import autoviz
df_520743312088167719 = autoviz.get_registered_df('df_520743312088167719')

def time_series_multiline(df, timelike_colname, value_colname, series_colname, figsize=(2.5, 1.3), mpl_palette_name='Dark2'):
  from matplotlib import pyplot as plt
  import seaborn as sns
  palette = list(sns.palettes.mpl_palette(mpl_palette_name))
  def _plot_series(series, series_name, series_index=0):
    if value_colname == 'count()':
      counted = (series[timelike_colname]
                 .value_counts()
                 .reset_index(name='counts')
                 .rename({'index': timelike_colname}, axis=1)
                 .sort_values(timelike_colname, ascending=True))
      xs = counted[timelike_colname]
      ys = counted['counts']
    else:
      xs = series[timelike_colname]
      ys = series[value_colname]
    plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

  fig, ax = plt.subplots(figsize=figsize, layout='constrained')
  df = df.sort_values(timelike_colname, ascending=True)
  if series_colname:
    for i, (series_name, series) in enumerate(df.groupby(series_colname)):
      _plot_series(series, series_name, i)
    fig.legend(title=series_colname, bbox_to_anchor=(1, 1), loc='upper left')
  else:
    _plot_series(df, '')
  sns.despine(fig=fig, ax=ax)
  plt.xlabel(timelike_colname)
  plt.ylabel(value_colname)
  return autoviz.MplChart.from_current_mpl_state()

chart = time_series_multiline(df_520743312088167719, *['index', 'count()', 'quetsion'], **{})
chart

import numpy as np
from google.colab import autoviz
df_520743312088167719 = autoviz.get_registered_df('df_520743312088167719')

def time_series_multiline(df, timelike_colname, value_colname, series_colname, figsize=(2.5, 1.3), mpl_palette_name='Dark2'):
  from matplotlib import pyplot as plt
  import seaborn as sns
  palette = list(sns.palettes.mpl_palette(mpl_palette_name))
  def _plot_series(series, series_name, series_index=0):
    if value_colname == 'count()':
      counted = (series[timelike_colname]
                 .value_counts()
                 .reset_index(name='counts')
                 .rename({'index': timelike_colname}, axis=1)
                 .sort_values(timelike_colname, ascending=True))
      xs = counted[timelike_colname]
      ys = counted['counts']
    else:
      xs = series[timelike_colname]
      ys = series[value_colname]
    plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

  fig, ax = plt.subplots(figsize=figsize, layout='constrained')
  df = df.sort_values(timelike_colname, ascending=True)
  if series_colname:
    for i, (series_name, series) in enumerate(df.groupby(series_colname)):
      _plot_series(series, series_name, i)
    fig.legend(title=series_colname, bbox_to_anchor=(1, 1), loc='upper left')
  else:
    _plot_series(df, '')
  sns.despine(fig=fig, ax=ax)
  plt.xlabel(timelike_colname)
  plt.ylabel(value_colname)
  return autoviz.MplChart.from_current_mpl_state()

chart = time_series_multiline(df_520743312088167719, *['index', 'count()', 'response'], **{})
chart

import numpy as np
from google.colab import autoviz
df_520743312088167719 = autoviz.get_registered_df('df_520743312088167719')

def time_series_multiline(df, timelike_colname, value_colname, series_colname, figsize=(2.5, 1.3), mpl_palette_name='Dark2'):
  from matplotlib import pyplot as plt
  import seaborn as sns
  palette = list(sns.palettes.mpl_palette(mpl_palette_name))
  def _plot_series(series, series_name, series_index=0):
    if value_colname == 'count()':
      counted = (series[timelike_colname]
                 .value_counts()
                 .reset_index(name='counts')
                 .rename({'index': timelike_colname}, axis=1)
                 .sort_values(timelike_colname, ascending=True))
      xs = counted[timelike_colname]
      ys = counted['counts']
    else:
      xs = series[timelike_colname]
      ys = series[value_colname]
    plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

  fig, ax = plt.subplots(figsize=figsize, layout='constrained')
  df = df.sort_values(timelike_colname, ascending=True)
  if series_colname:
    for i, (series_name, series) in enumerate(df.groupby(series_colname)):
      _plot_series(series, series_name, i)
    fig.legend(title=series_colname, bbox_to_anchor=(1, 1), loc='upper left')
  else:
    _plot_series(df, '')
  sns.despine(fig=fig, ax=ax)
  plt.xlabel(timelike_colname)
  plt.ylabel(value_colname)
  return autoviz.MplChart.from_current_mpl_state()

chart = time_series_multiline(df_520743312088167719, *['index', 'count()', 'answer'], **{})
chart

In [73]:
import evaluate
rouge = evaluate.load('rouge')
results = rouge.compute(predictions=predictions,references=references,use_stemmer=True)
results

{'rouge1': 0.48932914605331057,
 'rouge2': 0.186311546776425,
 'rougeL': 0.2908473528770049,
 'rougeLsum': 0.3179484429104119}

# Training

In [74]:
trainer = transformers.Trainer(
    model=model,
    train_dataset=train_dataset,
    # eval_dataset=val_dataset,
    args=transformers.TrainingArguments(
        num_train_epochs=1,
        per_device_train_batch_size=16,
        gradient_accumulation_steps=4,
        warmup_ratio=0.05,
        max_steps=100,
        learning_rate=2e-4,
        fp16=True,
        logging_steps=1,
        output_dir="outputs",
        optim="paged_adamw_8bit",
        lr_scheduler_type='cosine',
    ),
    data_collator=transformers.DataCollatorForLanguageModeling(tokenizer, mlm=False),
)
model.config.use_cache = False  # silence the warnings. Please re-enable for inference!
trainer.train()

<ipython-input-36-424aeced090c>:6: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  item = {key: torch.tensor(val[idx]) for key, val in self.encodings.items()}
You're using a PreTrainedTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=100, training_loss=1.385500727891922, metrics={'train_runtime': 4195.4574, 'train_samples_per_second': 1.525, 'train_steps_per_second': 0.024, 'total_flos': 3.1103569348460544e+16, 'train_loss': 1.385500727891922, 'epoch': 33.33})

# Example After Fine Tuning

In [75]:
model.config.use_cache = True
model.eval()

PeftModelForCausalLM(
  (base_model): LoraModel(
    (model): RWForCausalLM(
      (transformer): RWModel(
        (word_embeddings): Embedding(65025, 4544)
        (h): ModuleList(
          (0-31): 32 x DecoderLayer(
            (input_layernorm): LayerNorm((4544,), eps=1e-05, elementwise_affine=True)
            (self_attention): Attention(
              (maybe_rotary): RotaryEmbedding()
              (query_key_value): Linear4bit(
                in_features=4544, out_features=4672, bias=False
                (lora_dropout): ModuleDict(
                  (default): Dropout(p=0.05, inplace=False)
                )
                (lora_A): ModuleDict(
                  (default): Linear(in_features=4544, out_features=16, bias=False)
                )
                (lora_B): ModuleDict(
                  (default): Linear(in_features=16, out_features=4672, bias=False)
                )
                (lora_embedding_A): ParameterDict()
                (lora_embedding_B): Parameter

In [77]:
generate(0)

Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.


Question:
Define accountability in ESG context
Answer:
In the ESG (Environmental Social and Governance) context accountability refers to the responsibility of companies and organizations to account for their actions and decisions regarding environmental social and governance issues. This includes reporting on their performance transparency and disclosure of relevant information and ensuring that they are meeting regulatory standards and ethical standards. Accountability also involves taking responsibility for the impacts of a company's operations on society and the environment and actively engaging with stakeholders including investors customers employees and communities to address issues and promote positive change. Overall accountability is a critical component of responsible business practices and sustainable development. It helps to ensure that companies are meeting their stakeholders' expectations and contributing to a more sustainable and equitable future.
Best Answer:
In the ESG

In [78]:
prediction2 = get_response_set(model)

Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:11 for open-end generation.


In [79]:
results2 = rouge.compute(predictions=prediction2,references=references,use_stemmer=True)

In [81]:
results2

{'rouge1': 0.5382813240920763,
 'rouge2': 0.21855707395288354,
 'rougeL': 0.3228489567525088,
 'rougeLsum': 0.3546539687118282}

In [94]:
bleu = evaluate.load('bleu')
results_bleu = bleu.compute(predictions=predictions, references=references)
results_bleu2 = bleu.compute(predictions=prediction2, references=references)

print(results_bleu)
print(results_bleu2)

{'bleu': 0.12290265131562805, 'precisions': [0.45890968266883647, 0.1689909762100082, 0.08436724565756824, 0.043369474562135114], 'brevity_penalty': 0.9469434840047494, 'length_ratio': 0.9483024691358025, 'translation_length': 1229, 'reference_length': 1296}
{'bleu': 0.168672534752822, 'precisions': [0.47959914101646384, 0.19899062725306416, 0.11256354393609296, 0.0753474762253109], 'brevity_penalty': 1.0, 'length_ratio': 1.0779320987654322, 'translation_length': 1397, 'reference_length': 1296}


In [95]:
df

quetsion  \
0            Define sustainability in ESG context   
1  Define Chief Financial Officers in ESG context   
2                Define Green Deal in ESG context   
3    Define indigenous communities in ESG context   
4            Define B Impact Score in ESG context   
5    Define actively managed funds in ESG context   
6          Define climate disaster in ESG context   
7            Define green building in ESG context   
8           Define labor standards in ESG context   
9          Define Green Revolution in ESG context   

                                            response  \
0  Sustainability is a term that refers to the ab...   
1  Chief Financial Officers (CFOs) play a critica...   
2  Green Deal is a European Union initiative aime...   
3  Indigenous communities are groups of people wh...   
4  B Impact Score is a tool that measures the imp...   
5  Active management refers to the process of sel...   
6  Climate disaster refers to any event or phenom...   
7  Green building refers to the practice of desig...   
8  Labor standards refer to the minimum standards...   
9  Green Revolution refers to the period of time ...   

                                   my_model_response  \
0  Sustainability in the ESG (Environmental Socia...   
1  Chief Financial Officers (CFOs) in the ESG con...   
2  The Green Deal is a European Union initiative ...   
3  Indigenous communities refer to the original i...   
4  The B Impact Score is a tool developed by B La...   
5  Active management refers to the process of man...   
6  In the ESG (Environmental Social and Governanc...   
7  Green building in the ESG (Environmental Socia...   
8  In the context of ESG (Environmental Social an...   
9  Green Revolution refers to a period of social ...   

                                              answer  
0  Sustainability in the ESG (Environmental Socia...  
1  Chief Financial Officers (CFOs) in the ESG con...  
2  The Green Deal refers to a set of policies and...  
3  Indigenous communities refer to groups of peop...  
4  The B Impact Score is a comprehensive rating s...  
5  Actively managed funds are investment funds wh...  
6  In ESG (Environmental Social and Governance) c...  
7  Green building refers to the design constructi...  
8  Labor standards in ESG context refer to the gu...  
9  Green Revolution refers to a set of technologi...

# Merge Adapters and Save Model to Hub

In [82]:
from huggingface_hub import notebook_login

notebook_login()

In [83]:
model.save_pretrained("falcon-7b-instruct-ft-adapters-ESG-chatting", push_to_hub=True) # save LORA adapters
model.push_to_hub("falcon-7b-instruct-ft-adapters-ESG-chatting")

adapter_model.bin:   0%|          | 0.00/18.9M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/FelixChao/falcon-7b-instruct-ft-adapters-ESG-chatting/commit/761d05d2a2b1763dff47b5a4f0214832e429ffa7', commit_message='Upload model', commit_description='', oid='761d05d2a2b1763dff47b5a4f0214832e429ffa7', pr_url=None, pr_revision=None, pr_num=None)

In [ ]:
from transformers import AutoModelForCausalLM, PretrainedConfig
import torch

# reload the base model (you might need pro subscription for this)
model = AutoModelForCausalLM.from_pretrained("tiiuae/falcon-7b-instruct", device_map={"":0}, trust_remote_code=True, torch_dtype=torch.float16)


===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please run

python -m bitsandbytes

 and submit this information together with your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
bin /usr/local/lib/python3.10/dist-packages/bitsandbytes/libbitsandbytes_cuda118.so
CUDA_SETUP: WARNING! libcudart.so not found in any environmental path. Searching in backup paths...
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 7.5
CUDA SETUP: Detected CUDA version 118
CUDA SETUP: Loading binary /usr/local/lib/python3.10/dist-packages/bitsandbytes/libbitsandbytes_cuda118.so...


/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: /usr/lib64-nvidia did not contain ['libcudart.so', 'libcudart.so.11.0', 'libcudart.so.12.0'] as expected! Searching further paths...
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('/sys/fs/cgroup/memory.events /var/colab/cgroup/jupyter-children/memory.events')}
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('8013'), PosixPath('//172.28.0.1'), PosixPath('http')}
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('//colab.research.google.com/tun/m/cc483011

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [ ]:
from peft import PeftModel

# load perf model with new adapters
model = PeftModel.from_pretrained(
    model,
    "vrsen/falcon-7b-instruct-ft-adapters",
)

In [ ]:
model = model.merge_and_unload() # merge adapters with

In [ ]:
model.push_to_hub("falcon-7b-instruct-ft")

pytorch_model-00002-of-00002.bin:   0%|          | 0.00/3.89G [00:00<?, ?B/s]

Upload 2 LFS files:   0%|          | 0/2 [00:00<?, ?it/s]

pytorch_model-00001-of-00002.bin:   0%|          | 0.00/9.95G [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/vrsen/falcon-7b-instruct-ft/commit/93f6d84447abd80fff5ff062c81dc86b0ac72e82', commit_message='Upload RWForCausalLM', commit_description='', oid='93f6d84447abd80fff5ff062c81dc86b0ac72e82', pr_url=None, pr_revision=None, pr_num=None)

In [ ]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("tiiuae/falcon-7b-instruct", trust_remote_code=True)
tokenizer.push_to_hub("falcon-7b-instruct-ft", use_auth_token=True)

CommitInfo(commit_url='https://huggingface.co/vrsen/falcon-7b-instruct-ft/commit/ae7eca5a54426134be2babe2239380487dad3306', commit_message='Upload tokenizer', commit_description='', oid='ae7eca5a54426134be2babe2239380487dad3306', pr_url=None, pr_revision=None, pr_num=None)